In [4]:
import os
import numpy as np
import plotly.express as px
import matplotlib.pyplot as plt
from plotly.subplots import make_subplots
import pydicom as ds
from skimage import io
import cv2

In [5]:
def get_all_MRI(dirName):
    mri_list = os.listdir(dirName)
    all_MRI = []
    for file in mri_list:
        full_path = os.path.join(dirName, file)
        if os.path.isdir(full_path):
            all_MRI = all_MRI + get_all_MRI(full_path)
        else:
            all_MRI.append(full_path)
                
    return all_MRI

In [3]:
dataPath = 'PROSTATE-MRI/MIP-PROSTATE-01-0001/04-30-2006-MRI Prostate ERC-40831/401.000000-T2 TSE sag-01264'
files = get_all_MRI(dataPath)

In [10]:
patient_files = []

path = os.path.join(os.curdir, 'PROSTATE-MRI')
for index in range(1, 27):

    digit = f'0{index}' if index <= 9 else str(index)
    
    aux_path = os.path.join(path, f'MIP-PROSTATE-01-00{digit}')
    aux_path = os.path.join(aux_path, os.listdir(aux_path)[0])
    
    files = []
    
    for directory in os.listdir(aux_path):
        directory_path = os.path.join(aux_path, directory)
        directory_files = get_all_MRI(directory_path)
        files.append(directory_files)
    
    patient_files.append(files)

In [16]:
patient = 3
graph = 5

image_set = []
for file in patient_files[patient][graph]:
    image = ds.dcmread(file).pixel_array
    image_set.append(image)

combined_image = image_set[0].copy()
for i in range(1, len(image_set)):
    combined_image += image_set[i]

px.imshow(combined_image, color_continuous_scale='gray')

In [17]:
px.imshow(image_set[-1], color_continuous_scale='gray')

In [78]:
HOUNSFIELD_MIN = -1_000
HOUNSFIELD_MAX = 2_000
HOUNSFIELD_RANGE = HOUNSFIELD_MAX - HOUNSFIELD_MIN

def normalize_intensity(img):
    img[img < HOUNSFIELD_MIN] = HOUNSFIELD_MIN
    img[img > HOUNSFIELD_MAX] = HOUNSFIELD_MAX
    
    return (img - HOUNSFIELD_MIN) / HOUNSFIELD_RANGE

n_img = normalize_intensity(combined_image)

In [79]:
px.imshow(n_img, color_continuous_scale='gray')

In [57]:
def save_slice(img, fname, path):
    img = np.uint8(img + 255)
    fout = os.path.join(path, f'{fname}.png')
    cv2.imwrite(fout, img)

In [58]:
px.imshow(n_img[50: 100, 15:75], color_continuous_scale='gray')

## U net

In [6]:
import tensorflow as tf
from tensorflow.keras import layers

IMG_WIDTH = 128
IMG_HEIGHT = 128
IMG_CHANNELS = 3

inputs = layers.Input((IMG_WIDTH, IMG_HEIGHT, IMG_CHANNELS))
s = layers.Lambda(lambda x: x / 255.0)(inputs)

c1 = tf.keras.layers.Conv2D(16, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(s)
c1 = tf.keras.layers.Dropout(0.1)(c1)
c1 = tf.keras.layers.Conv2D(16, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(c1)
p1 = tf.keras.layers.MaxPooling2D((2, 2))(c1)

c2 = tf.keras.layers.Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(p1)
c2 = tf.keras.layers.Dropout(0.1)(c2)
c2 = tf.keras.layers.Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(c2)
p2 = tf.keras.layers.MaxPooling2D((2, 2))(c2)
 
c3 = tf.keras.layers.Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(p2)
c3 = tf.keras.layers.Dropout(0.2)(c3)
c3 = tf.keras.layers.Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(c3)
p3 = tf.keras.layers.MaxPooling2D((2, 2))(c3)
 
c4 = tf.keras.layers.Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(p3)
c4 = tf.keras.layers.Dropout(0.2)(c4)
c4 = tf.keras.layers.Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(c4)
p4 = tf.keras.layers.MaxPooling2D(pool_size=(2, 2))(c4)
 
c5 = tf.keras.layers.Conv2D(256, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(p4)
c5 = tf.keras.layers.Dropout(0.3)(c5)
c5 = tf.keras.layers.Conv2D(256, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(c5)

u6 = tf.keras.layers.Conv2DTranspose(128, (2, 2), strides=(2, 2), padding='same')(c5)
u6 = tf.keras.layers.concatenate([u6, c4])
c6 = tf.keras.layers.Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(u6)
c6 = tf.keras.layers.Dropout(0.2)(c6)
c6 = tf.keras.layers.Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(c6)
 
u7 = tf.keras.layers.Conv2DTranspose(64, (2, 2), strides=(2, 2), padding='same')(c6)
u7 = tf.keras.layers.concatenate([u7, c3])
c7 = tf.keras.layers.Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(u7)
c7 = tf.keras.layers.Dropout(0.2)(c7)
c7 = tf.keras.layers.Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(c7)
 
u8 = tf.keras.layers.Conv2DTranspose(32, (2, 2), strides=(2, 2), padding='same')(c7)
u8 = tf.keras.layers.concatenate([u8, c2])
c8 = tf.keras.layers.Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(u8)
c8 = tf.keras.layers.Dropout(0.1)(c8)
c8 = tf.keras.layers.Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(c8)
 
u9 = tf.keras.layers.Conv2DTranspose(16, (2, 2), strides=(2, 2), padding='same')(c8)
u9 = tf.keras.layers.concatenate([u9, c1], axis=3)
c9 = tf.keras.layers.Conv2D(16, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(u9)
c9 = tf.keras.layers.Dropout(0.1)(c9)
c9 = tf.keras.layers.Conv2D(16, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(c9)

outputs = layers.Conv2D(1, (1, 1), activation='sigmoid')(c9)

model = tf.keras.Model(inputs = [inputs], outputs = [outputs])
model.compile(optimizer = 'adam', loss = 'binary_crossentropy', metrics = ['accuracy'])
model.summary()

Model: "functional_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, 128, 128, 3) 0                                            
__________________________________________________________________________________________________
lambda (Lambda)                 (None, 128, 128, 3)  0           input_1[0][0]                    
__________________________________________________________________________________________________
conv2d (Conv2D)                 (None, 128, 128, 16) 448         lambda[0][0]                     
__________________________________________________________________________________________________
dropout (Dropout)               (None, 128, 128, 16) 0           conv2d[0][0]                     
_______________________________________________________________________________________

In [7]:
import tensorflow_datasets as tfds

def normalize(input_image, input_mask):
    input_image = tf.cast(input_image, tf.float32) / 255.0
    input_mask -= 1
    return input_image, input_mask

@tf.function
def load_image_train(datapoint):
    input_image = tf.image.resize(datapoint['image'], (128, 128))
    input_mask = tf.image.resize(datapoint['segmentation_mask'], (128, 128))

    if tf.random.uniform(()) > 0.5:
        input_image = tf.image.flip_left_right(input_image)
        input_mask = tf.image.flip_left_right(input_mask)

    input_image, input_mask = normalize(input_image, input_mask)

    return input_image, input_mask

def load_image_test(datapoint):
    input_image = tf.image.resize(datapoint['image'], (128, 128))
    input_mask = tf.image.resize(datapoint['segmentation_mask'], (128, 128))

    input_image, input_mask = normalize(input_image, input_mask)

    return input_image, input_mask

dataset, info = tfds.load('oxford_iiit_pet:3.*.*', with_info=True)

TRAIN_LENGTH = info.splits['train'].num_examples
BATCH_SIZE = 1
BUFFER_SIZE = 1000
STEPS_PER_EPOCH = TRAIN_LENGTH // BATCH_SIZE

train = dataset['train'].map(load_image_train, num_parallel_calls=tf.data.experimental.AUTOTUNE)
test = dataset['test'].map(load_image_test)

train_dataset = train.cache().shuffle(BUFFER_SIZE).batch(BATCH_SIZE).repeat()
train_dataset = train_dataset.prefetch(buffer_size = tf.data.experimental.AUTOTUNE)
test_dataset = test.batch(BATCH_SIZE)

In [8]:
checkpoints = tf.keras.callbacks.ModelCheckpoint('model_checkpt.h5', verbose = 1, save_best_only=True)
early = tf.keras.callbacks.EarlyStopping(patience = 2, monitor = 'val_loss')
tensorboard = tf.keras.callbacks.TensorBoard(log_dir = 'logs')

results = model.fit(
    train_dataset, validation_data = test_dataset, 
    batch_size = 16, 
    steps_per_epoch = STEPS_PER_EPOCH,
    epochs = 3, callbacks = [checkpoints, early, tensorboard]
)

Epoch 1/3
   1/3680 [..............................] - ETA: 0s - loss: 0.6927 - accuracy: 0.5973WARNING:tensorflow:From c:\python\lib\site-packages\tensorflow\python\ops\summary_ops_v2.py:1277: stop (from tensorflow.python.eager.profiler) is deprecated and will be removed after 2020-07-01.
Instructions for updating:
use `tf.profiler.experimental.stop` instead.


Instructions for updating:
use `tf.profiler.experimental.stop` instead.


   2/3680 [..............................] - ETA: 25:58 - loss: 0.6879 - accuracy: 0.5652WARNING:tensorflow:Callbacks method `on_train_batch_end` is slow compared to the batch time (batch time: 0.1476s vs `on_train_batch_end` time: 0.6987s). Check your callbacks.


3285/3680 [=========================>....] - ETA: 1:07 - loss: nan - accuracy: 0.5181

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "c:\python\lib\site-packages\IPython\core\interactiveshell.py", line 3417, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-8-b069c9d427a1>", line 5, in <module>
    results = model.fit(
  File "c:\python\lib\site-packages\tensorflow\python\keras\engine\training.py", line 108, in _method_wrapper
    return method(self, *args, **kwargs)
  File "c:\python\lib\site-packages\tensorflow\python\keras\engine\training.py", line 1098, in fit
    tmp_logs = train_function(iterator)
  File "c:\python\lib\site-packages\tensorflow\python\eager\def_function.py", line 780, in __call__
    result = self._call(*args, **kwds)
  File "c:\python\lib\site-packages\tensorflow\python\eager\def_function.py", line 807, in _call
    return self._stateless_fn(*args, **kwds)  # pylint: disable=not-callable
  File "c:\python\lib\site-packages\tensorflow\python\eager\function.py", line 2829, in __call__
    return graph_function._filt

TypeError: object of type 'NoneType' has no len()

In [107]:
img = io.imread('dog_net.jpg')
img_res = cv2.resize(img, dsize=(128, 128), interpolation=cv2.INTER_CUBIC).reshape(1, 128, 128, 3)
img_pred = model.predict(img_res)